In [2]:
import argparse
import logging
import os
import sys

import numpy as np
import torch
import torch.nn as nn
from torch import optim
from tqdm import tqdm

from eval import eval_net
from unet import UNet

from torch.utils.tensorboard import SummaryWriter
from utils.dataset import BasicDataset
from torch.utils.data import DataLoader, random_split

from IPython.display import clear_output

In [3]:
dir_img = '/home/ubuntu/T2_Sag_FL/train_data/imgs/'
dir_mask = '/home/ubuntu/T2_Sag_FL/train_data/masks/'

dir_checkpoint = 'ckpts_dir/fl_ckpts/'

try:
# Create target Directory
    os.mkdir(dir_checkpoint)
    print("Directory " , dir_checkpoint ,  " Created ") 
except FileExistsError:
    print("Directory " , dir_checkpoint ,  " already exists")

Directory  ckpts_dir/fl_ckpts/  already exists


In [29]:
def train_net(net,
              device,
              epochs=5,
              batch_size=1,
              lr=0.001,
              val_percent=0.1,
              save_cp=True,
              img_scale=0.5,
              epoch_bias = 0):

    dataset = BasicDataset(dir_img, dir_mask, img_scale)
    n_val = int(len(dataset) * val_percent)
    n_train = len(dataset) - n_val
    train, val = random_split(dataset, [n_train, n_val])
    train_loader = DataLoader(train, batch_size=batch_size, shuffle=True, num_workers=8, pin_memory=True)
    val_loader = DataLoader(val, batch_size=batch_size, shuffle=False, num_workers=8, pin_memory=True, drop_last=True)

    writer = SummaryWriter(comment=f'LR_{lr}_BS_{batch_size}_SCALE_{img_scale}')
    global_step = 0

    logging.info(f'''Starting training:
        Epochs:          {epochs}
        Batch size:      {batch_size}
        Learning rate:   {lr}
        Training size:   {n_train}
        Validation size: {n_val}
        Checkpoints:     {save_cp}
        Device:          {device.type}
        Images scaling:  {img_scale}
    ''')

    optimizer = optim.RMSprop(net.parameters(), lr=lr, weight_decay=1e-8, momentum=0.9)
    scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, 'min' if net.n_classes > 2 else 'max', patience=2)
    if net.n_classes > 2:
        print("Using CrossEntropyLoss")
        criterion = nn.CrossEntropyLoss()
    else:
        print("Using BCEWithLogitsLoss")
        criterion = nn.BCEWithLogitsLoss()

    for epoch in range(epochs):
        net.train()

        epoch_loss = 0
        with tqdm(total=n_train, desc=f'Epoch {epoch + 1}/{epochs}', unit='img') as pbar:
            for batch in train_loader:
                imgs = batch['image']
                true_masks = batch['mask']
                
                assert imgs.shape[1] == net.n_channels, \
                    f'Network has been defined with {net.n_channels} input channels, ' \
                    f'but loaded images have {imgs.shape[1]} channels. Please check that ' \
                    'the images are loaded correctly.'

                imgs = imgs.to(device=device, dtype=torch.float32)
                mask_type = torch.float32 if net.n_classes <= 2 else torch.long
                true_masks = true_masks.to(device=device, dtype=mask_type)

                masks_pred = net(imgs)
                
                loss = criterion(masks_pred, true_masks)
                epoch_loss += loss.item()
                writer.add_scalar('Loss/train', loss.item(), global_step)

                pbar.set_postfix(**{'loss (batch)': loss.item()})

                optimizer.zero_grad()
                loss.backward()
                nn.utils.clip_grad_value_(net.parameters(), 0.1)
                optimizer.step()

                pbar.update(imgs.shape[0])
                global_step += 1
                if global_step % (len(dataset) // (10 * batch_size)) == 0:
                    for tag, value in net.named_parameters():
                        tag = tag.replace('.', '/')
                        writer.add_histogram('weights/' + tag, value.data.cpu().numpy(), global_step)
                        writer.add_histogram('grads/' + tag, value.grad.data.cpu().numpy(), global_step)

                    val_score = eval_net(net, val_loader, device)
                    scheduler.step(val_score)
                    writer.add_scalar('learning_rate', optimizer.param_groups[0]['lr'], global_step)

                    if net.n_classes > 2:
                        logging.info('Validation cross entropy: {}'.format(val_score))
                        writer.add_scalar('Loss/test', val_score, global_step)
                    else:
                        logging.info('Validation Dice Coeff: {}'.format(val_score))
                        writer.add_scalar('Dice/test', val_score, global_step)

                    writer.add_images('images', imgs, global_step)
                    if net.n_classes == 1:
                        writer.add_images('masks/true', true_masks, global_step)
                        writer.add_images('masks/pred', torch.sigmoid(masks_pred) > 0.5, global_step)

        if save_cp:
            try:
                os.mkdir(dir_checkpoint)
                logging.info('Created checkpoint directory')
            except OSError:
                pass
            if (epoch + epoch_bias + 1) % 50 == 0:
                torch.save(net.state_dict(),
                           dir_checkpoint + f'CP_epoch{epoch + epoch_bias + 1}.pth')
                logging.info(f'Checkpoint {epoch + epoch_bias + 1} saved !')

    writer.close()

In [30]:
logging.basicConfig(level=logging.INFO, format='%(levelname)s: %(message)s')
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
logging.info(f'Using device {device}')

INFO: Using device cuda


In [31]:
n_classes = 2 
n_channels = 1 

In [32]:
net = UNet(n_channels=n_channels, n_classes=n_classes, bilinear=True)
logging.info(f'Network:\n'
             f'\t{net.n_channels} input channels\n'
             f'\t{net.n_classes} output channels (classes)\n'
             f'\t{"Bilinear" if net.bilinear else "Transposed conv"} upscaling')

INFO: Network:
	1 input channels
	2 output channels (classes)
	Bilinear upscaling


In [17]:
epochs = 100 
batchsize = 16

load = False
epoch_bias = 0

In [18]:
if load:
    net.load_state_dict(
        torch.load(load, map_location=device)
    )
    logging.info(f'Model loaded from {load}')

net.to(device=device)

# clear_output()


try:
    train_net(net=net,
              epochs=epochs,
              batch_size=batchsize,
              device=device,
              epoch_bias=epoch_bias)
except KeyboardInterrupt:
    torch.save(net.state_dict(), 'INTERRUPTED.pth')
    logging.info('Saved interrupt')
    try:
        sys.exit(0)
    except SystemExit:
        os._exit(0)

INFO: Creating dataset with 1414 examples
INFO: Starting training:
        Epochs:          100
        Batch size:      16
        Learning rate:   0.001
        Training size:   1273
        Validation size: 141
        Checkpoints:     True
        Device:          cuda
        Images scaling:  0.5
    
Epoch 1/100:   0%|          | 0/1273 [00:00<?, ?img/s]

Using BCEWithLogitsLoss


Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.93batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  3.00batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  3.00batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.97batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  3.06batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  3.02batch/s]
             

Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.90batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Epoch 2/100: 100%|██████████| 1273/1273 [02:15<00:00,  9.38img/s, loss (batch)=0.0031]
INFO: Checkpoint 2 saved !
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.99batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.98batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.98batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.88batch/s]
                                                                  INFO: Validation 

                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.94batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Epoch 4/100: 100%|██████████| 1273/1273 [02:17<00:00,  9.28img/s, loss (batch)=0.00375]
INFO: Checkpoint 4 saved !
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.95batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.94batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.87batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|█████████

...

Validation round: 100%|██████████| 8/8 [00:02<00:00,  3.01batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.90batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.90batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.85batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.89batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.88batch/s]
             

Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.92batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.86batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.97batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.95batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.92batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.92batch/s]
             

Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.93batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.86batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.85batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.95batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.85batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.86batch/s]
             

Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.96batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  3.03batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.87batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.89batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.87batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.91batch/s]
             

Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.90batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.99batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.89batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.97batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:03<00:00,  2.87batch/s]
                                                                  INFO: Validation Dice Coeff: 2.012982534438379e-06
Validation round: 100%|██████████| 8/8 [00:02<00:00,  2.94batch/s]
             

In [19]:
epochs = 100 
batchsize = 8

load = dir_checkpoint+'CP_epoch100.pth'
epoch_bias = 100

In [20]:
if load:
    net.load_state_dict(
        torch.load(load, map_location=device)
    )
    logging.info(f'Model loaded from {load}')

net.to(device=device)

# clear_output()


try:
    train_net(net=net,
              epochs=epochs,
              batch_size=batchsize,
              device=device,
              epoch_bias=epoch_bias)
except KeyboardInterrupt:
    torch.save(net.state_dict(), 'INTERRUPTED.pth')
    logging.info('Saved interrupt')
    try:
        sys.exit(0)
    except SystemExit:
        os._exit(0)

INFO: Model loaded from ckpts_dir/fl_ckpts/CP_epoch100.pth
INFO: Creating dataset with 1414 examples
INFO: Starting training:
        Epochs:          100
        Batch size:      8
        Learning rate:   0.001
        Training size:   1273
        Validation size: 141
        Checkpoints:     True
        Device:          cuda
        Images scaling:  0.5
    
Epoch 1/100:   0%|          | 0/1273 [00:00<?, ?img/s]

Using BCEWithLogitsLoss


Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.54batch/s]
                                                                    INFO: Validation Dice Coeff: 2.0549547477511464e-06
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.50batch/s]
                                                                    INFO: Validation Dice Coeff: 2.0549547477511464e-06
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.51batch/s]
                                                                    INFO: Validation Dice Coeff: 2.0549547477511464e-06
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.51batch/s]
                                                                    INFO: Validation Dice Coeff: 0.004407234347367835
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.52batch/s]
                                                                    INFO: Validation Dice Coeff: 0.0042912585741653264
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.

Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.48batch/s]
                                                                    INFO: Validation Dice Coeff: 0.04308749609352911
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.51batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5225094118539024
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
                                                                    INFO: Validation Dice Coeff: 0.4525247987578897
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.49batch/s]
                                                                    INFO: Validation Dice Coeff: 0.04917811251738492
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.49batch/s]
                                                                    INFO: Validation Dice Coeff: 0.4514347297303817
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.44batch/s]
    

Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5275305018705481
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.48batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5714927911758423
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5752185583114624
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.43batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5812547873048222
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.48batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5792496660176445
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.44batch/s]
      

...

Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5755157716134015
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.45batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5788939945838031
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.46batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5788847313207739
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.46batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5766047624980702
Epoch 96/100: 100%|██████████| 1273/1273 [02:29<00:00,  8.54img/s, loss (batch)=0.00175] 
INFO: Checkpoint 196 saved !
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.48batch/s]
                                                                    INFO

Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5752002000808716
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.46batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5719893381876104
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5739296429297503
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.48batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5782618733013377
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.44batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5757094796966103
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.43batch/s]
      

Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.43batch/s]
                                                                    INFO: Validation Dice Coeff: 0.572862751343671
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.46batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5750297483275918
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.45batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5769059377558091
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.44batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5724318956627565
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.43batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5788303788970498
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
       

Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.48batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5794886771370383
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.45batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5785588499377755
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.45batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5795569735414842
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.43batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5727711214738733
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.47batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5752320464919595
Epoch 99/100: 100%|██████████| 1273/1273 [02:29<00:00,  8.54img/s, loss (ba

Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.46batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5690538567655227
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.46batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5743599376257729
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.49batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5782109218485215
Validation round: 100%|██████████| 17/17 [00:03<00:00,  5.45batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5767461517277885
Epoch 100/100: 100%|██████████| 1273/1273 [02:36<00:00,  8.11img/s, loss (batch)=0.000843]
INFO: Checkpoint 200 saved !


In [21]:
epochs = 50 
batchsize = 4

load = dir_checkpoint+'CP_epoch200.pth'
epoch_bias = 200

In [22]:
if load:
    net.load_state_dict(
        torch.load(load, map_location=device)
    )
    logging.info(f'Model loaded from {load}')

net.to(device=device)

# clear_output()

try:
    train_net(net=net,
              epochs=epochs,
              batch_size=batchsize,
              device=device,
              epoch_bias=epoch_bias)
except KeyboardInterrupt:
    torch.save(net.state_dict(), 'INTERRUPTED.pth')
    logging.info('Saved interrupt')
    try:
        sys.exit(0)
    except SystemExit:
        os._exit(0)

INFO: Model loaded from ckpts_dir/fl_ckpts/CP_epoch200.pth
INFO: Creating dataset with 1414 examples
INFO: Starting training:
        Epochs:          50
        Batch size:      4
        Learning rate:   0.001
        Training size:   1273
        Validation size: 141
        Checkpoints:     True
        Device:          cuda
        Images scaling:  0.5
    
Epoch 1/50:   0%|          | 0/1273 [00:00<?, ?img/s]

Using BCEWithLogitsLoss


Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.21batch/s]
                                                                    INFO: Validation Dice Coeff: 0.228448637681348
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.23batch/s]
                                                                    INFO: Validation Dice Coeff: 0.2633149862289429
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.525779184273311
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.24batch/s]
                                                                    INFO: Validation Dice Coeff: 0.08834351204758864
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.43119860802377974
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.21batch/s]
      

Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.21batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6019402384757996
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.21batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6411708899906703
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.24batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5952558585575649
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.30batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6098910093307495
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.23batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5841379889420101
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.24batch/s]
      

Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.24batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6374294945171901
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6314711119447436
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.24batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6336769419057029
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6369568024362836
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.23batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6361407228878566
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.24batch/s]
      

...

Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.28batch/s]
                                                                    INFO: Validation Dice Coeff: 0.641389525788171
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6369905880519322
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.27batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6375311698232379
Epoch 45/50: 100%|██████████| 1273/1273 [02:36<00:00,  8.14img/s, loss (batch)=0.000296]
INFO: Checkpoint 245 saved !
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.29batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6386254685265678
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.22batch/s]
                                                                    INFO: 

Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.20batch/s]
                                                                    INFO: Validation Dice Coeff: 0.633770477771759
Epoch 46/50: 100%|██████████| 1273/1273 [02:35<00:00,  8.16img/s, loss (batch)=0.000595]
INFO: Checkpoint 246 saved !
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.27batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6395415578569684
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.25batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6333893844059535
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.30batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6339229438986097
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.25batch/s]
                                                                    INFO: 

Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.27batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6342794648238591
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.24batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6383687266281672
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.23batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6379240104130336
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.25batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6343592320169721
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.26batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6356996859822954
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.28batch/s]
      

Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.24batch/s]
                                                                    INFO: Validation Dice Coeff: 0.637932345696858
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.24batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6337156219141824
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.23batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6388635584286281
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.20batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6356966921261379
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.27batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6351344687598092
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.18batch/s]
       

Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.23batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6373438545635768
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.21batch/s]
                                                                    INFO: Validation Dice Coeff: 0.632098776102066
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.21batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6371098041534424
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.28batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6377891302108765
Validation round: 100%|██████████| 35/35 [00:03<00:00, 10.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6355417447430747
Validation round:  97%|█████████▋| 34/35 [00:03<00:00, 10.25batch/s]
       

In [23]:
epochs = 50 
batchsize = 2

load = dir_checkpoint+'CP_epoch250.pth'
epoch_bias = 250

In [ ]:
if load:
    net.load_state_dict(
        torch.load(load, map_location=device)
    )
    logging.info(f'Model loaded from {load}')

net.to(device=device)

# clear_output()

try:
    train_net(net=net,
              epochs=epochs,
              batch_size=batchsize,
              device=device,
              epoch_bias=epoch_bias)
except KeyboardInterrupt:
    torch.save(net.state_dict(), 'INTERRUPTED.pth')
    logging.info('Saved interrupt')
    try:
        sys.exit(0)
    except SystemExit:
        os._exit(0)

INFO: Model loaded from ckpts_dir/fl_ckpts/CP_epoch250.pth
INFO: Creating dataset with 1414 examples
INFO: Starting training:
        Epochs:          50
        Batch size:      2
        Learning rate:   0.001
        Training size:   1273
        Validation size: 141
        Checkpoints:     True
        Device:          cuda
        Images scaling:  0.5
    
Epoch 1/50:   0%|          | 0/1273 [00:00<?, ?img/s]

Using BCEWithLogitsLoss


Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.556997948884964
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.25batch/s]
                                                                    INFO: Validation Dice Coeff: 0.3768905580648217
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.19batch/s]
                                                                    INFO: Validation Dice Coeff: 0.5806961297988892
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.28batch/s]
                                                                    INFO: Validation Dice Coeff: 0.4305213720670768
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.20batch/s]
                                                                    INFO: Validation Dice Coeff: 0.3549576534756592
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.19batch/s]
       

Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.624500026021685
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.28batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6385866799524852
Epoch 1/50: 100%|██████████| 1273/1273 [02:42<00:00,  7.84img/s, loss (batch)=0.000481]
INFO: Checkpoint 251 saved !
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.28batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6434540829488209
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.26batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6146952697208949
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.20batch/s]
                                                                    INFO: V

Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.23batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6392815372773579
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.25batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6400292430605207
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.18batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6377229477678027
Epoch 2/50: 100%|██████████| 1273/1273 [02:42<00:00,  7.84img/s, loss (batch)=0.000506]
INFO: Checkpoint 252 saved !
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.27batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6415430358478001
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.19batch/s]
                                                                    INFO: 

Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.20batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6399968504905701
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.20batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6346624608550753
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6391465242419924
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.21batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6368215526853289
Epoch 3/50: 100%|██████████| 1273/1273 [02:42<00:00,  7.84img/s, loss (batch)=0.00035] 
INFO: Checkpoint 253 saved !
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.26batch/s]
                                                                    INFO: 

Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.22batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6361093240124839
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.25batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6371797374316625
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.12batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6407511855874742
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.20batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6369033856051308
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.16batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6371603148324149
Epoch 4/50: 100%|██████████| 1273/1273 [02:41<00:00,  7.87img/s, loss (batc

Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.11batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6367932945489884
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.10batch/s]
                                                                    INFO: Validation Dice Coeff: 0.642109220794269
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.11batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6311223749603544
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.14batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6371619531086513
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.15batch/s]
                                                                    INFO: Validation Dice Coeff: 0.635344209415572
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.19batch/s]
        

Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.15batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6411323755979538
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.09batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6408485191208976
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.08batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6408311166933605
Validation round:  97%|█████████▋| 68/70 [00:03<00:00, 20.16batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6268901799406325
Validation round: 100%|██████████| 70/70 [00:03<00:00, 20.12batch/s]
                                                                    INFO: Validation Dice Coeff: 0.6354294125522886
Validation round:  99%|█████████▊| 69/70 [00:03<00:00, 20.13batch/s]
      

In [ ]:
epochs = 50 
batchsize = 1

load = dir_checkpoint+'CP_epoch300.pth'
epoch_bias = 300

In [ ]:
if load:
    net.load_state_dict(
        torch.load(load, map_location=device)
    )
    logging.info(f'Model loaded from {load}')

net.to(device=device)

# clear_output()

try:
    train_net(net=net,
              epochs=epochs,
              batch_size=batchsize,
              device=device,
              epoch_bias=epoch_bias)
except KeyboardInterrupt:
    torch.save(net.state_dict(), 'INTERRUPTED.pth')
    logging.info('Saved interrupt')
    try:
        sys.exit(0)
    except SystemExit:
        os._exit(0)

In [ ]:
################################## упало, возобновляем

In [33]:
epochs = 41
batchsize = 1

load = dir_checkpoint+'CP_epoch309.pth'
epoch_bias = 309

In [34]:
if load:
    net.load_state_dict(
        torch.load(load, map_location=device)
    )
    logging.info(f'Model loaded from {load}')

net.to(device=device)

# clear_output()

try:
    train_net(net=net,
              epochs=epochs,
              batch_size=batchsize,
              device=device,
              epoch_bias=epoch_bias)
except KeyboardInterrupt:
    torch.save(net.state_dict(), 'INTERRUPTED.pth')
    logging.info('Saved interrupt')
    try:
        sys.exit(0)
    except SystemExit:
        os._exit(0)

INFO: Model loaded from ckpts_dir/fl_ckpts/CP_epoch309.pth
INFO: Creating dataset with 1414 examples
INFO: Starting training:
        Epochs:          41
        Batch size:      1
        Learning rate:   0.001
        Training size:   1273
        Validation size: 141
        Checkpoints:     True
        Device:          cuda
        Images scaling:  0.5
    
Epoch 1/41:   0%|          | 0/1273 [00:00<?, ?img/s]

Using BCEWithLogitsLoss


Validation round:  97%|█████████▋| 137/141 [00:03<00:00, 43.19batch/s]
                                                                      INFO: Validation Dice Coeff: 0.5128765377237051
Validation round:  98%|█████████▊| 138/141 [00:03<00:00, 42.89batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6307283216471865
Validation round:  97%|█████████▋| 137/141 [00:03<00:00, 42.31batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6163235889676687
Validation round:  97%|█████████▋| 137/141 [00:03<00:00, 41.85batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6124469635164389
Validation round:  98%|█████████▊| 138/141 [00:03<00:00, 41.80batch/s]
                                                                      INFO: Validation Dice Coeff: 0.5795002085195063
Validation round:  98%|█████████▊| 138/141 [00:03<00:00

Validation round:  98%|█████████▊| 138/141 [00:03<00:00, 41.19batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6471552322293285
Validation round:  97%|█████████▋| 137/141 [00:03<00:00, 41.02batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6422245579339457
Validation round:  97%|█████████▋| 137/141 [00:03<00:00, 40.80batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6427015757268029
Epoch 1/41: 100%|██████████| 1273/1273 [02:38<00:00,  8.04img/s, loss (batch)=0.000361]
INFO: Checkpoint 310 saved !
Validation round:  97%|█████████▋| 137/141 [00:03<00:00, 40.51batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6590034856139549
Validation round:  98%|█████████▊| 138/141 [00:03<00:00, 40.32batch/s]
                                                        

Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.75batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6400307200786919
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.61batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6583327121306463
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.55batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6456221819582516
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.59batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6533358118483067
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.50batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6520930198098911
Epoch 2/41: 100%|██████████| 1273/1273 [02:43<00:00,  7

...

Validation round:  98%|█████████▊| 138/141 [00:03<00:00, 39.55batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6526351895632931
Epoch 38/41: 100%|██████████| 1273/1273 [02:44<00:00,  7.72img/s, loss (batch)=0.000289]
INFO: Checkpoint 347 saved !
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.65batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6584879170715685
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.68batch/s]
                                                                      INFO: Validation Dice Coeff: 0.655183670846219
Validation round: 100%|██████████| 141/141 [00:03<00:00, 39.47batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6541988746504467
Validation round: 100%|██████████| 141/141 [00:03<00:00, 39.65batch/s]
                                                        

Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.56batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6550276555693563
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.65batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6528964949416883
Validation round: 100%|██████████| 141/141 [00:03<00:00, 39.69batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6546180671401247
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.51batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6501871225915482
Epoch 39/41: 100%|██████████| 1273/1273 [02:44<00:00,  7.72img/s, loss (batch)=0.000669]
INFO: Checkpoint 348 saved !
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.67batch/s]
                                                       

Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.63batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6587262119981022
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.62batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6575416153637286
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.45batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6584220828088724
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.72batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6609071011625058
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.54batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6524394879374898
Validation round:  59%|█████▉    | 83/141 [00:02<00:01,

Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.67batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6473063150647684
Validation round: 100%|██████████| 141/141 [00:03<00:00, 39.63batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6495190649707917
Epoch 40/41: 100%|██████████| 1273/1273 [02:44<00:00,  7.73img/s, loss (batch)=0.000669]
INFO: Checkpoint 349 saved !
Validation round: 100%|██████████| 141/141 [00:03<00:00, 39.59batch/s]
                                                                      INFO: Validation Dice Coeff: 0.651498200461379
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.58batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6526713740590128
Validation round:  97%|█████████▋| 137/141 [00:03<00:00, 39.84batch/s]
                                                        

Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.76batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6522769388848118
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.62batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6533923080398361
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.58batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6550602823467074
Validation round:  99%|█████████▉| 140/141 [00:03<00:00, 39.57batch/s]
                                                                      INFO: Validation Dice Coeff: 0.6517908844959077
Validation round:  99%|█████████▊| 139/141 [00:03<00:00, 39.56batch/s]
                                                                      INFO: Validation Dice Coeff: 0.651308369307865
Epoch 41/41: 100%|██████████| 1273/1273 [02:45<00:00,  7